In [1]:
from SPARQLWrapper import SPARQLWrapper, JSON

In [5]:

sparql = SPARQLWrapper(
    "https://polifonia.disi.unibo.it/choco/sparql"
)
sparql.setReturnFormat(JSON)
sparql.setQuery("""
PREFIX rdf: <http://www.w3.org/1999/02/22-rdf-syntax-ns#>
PREFIX rdfs: <http://www.w3.org/2000/01/rdf-schema#>
PREFIX jams: <http://w3id.org/polifonia/ontology/jams/>
PREFIX core: <http://w3id.org/polifonia/ontology/core/>
PREFIX pftype: <http://w3id.org/polifonia/resource/ValueType/>
PREFIX prov: <http://www.w3.org/ns/prov#>
PREFIX mm: <http://w3id.org/polifonia/ontology/music-entity/>
PREFIX owl: <http://www.w3.org/2002/07/owl#>

SELECT DISTINCT ?chocoId ?key_observation
WHERE {
  ?musicentity a mm:MusicEntity ;
    jams:hasJAMSAnnotation ?annotation .
  ?annotation jams:hasAnnotationType ?chordType ;
    prov:wasDerivedFrom ?jamsFile .
  ?jamsFile owl:sameAs ?chocoLink ;
    rdfs:label ?chocoId .
  ?jamsFile a jams:JAMSFile ;
    rdfs:label ?queryID .
  ?annotation a jams:JAMSAnnotation ;
    prov:wasDerivedFrom ?jamsFile ;
    jams:hasAnnotationType "chord_harte" ;
    jams:includesObservation ?observation .
  ?observation jams:hasMusicTimeInterval [jams:hasMusicTimeDuration [ jams:hasValue ?duration ; jams:hasValueType pftype:Beat]] .
    
                
  ?key_annotation a jams:JAMSAnnotation ;
    prov:wasDerivedFrom ?jamsFile ;
    jams:includesObservation/rdfs:label ?key_observation ;
    jams:hasAnnotationType "key_mode" . 
}
# GROUP BY (?chocoId)
# HAVING (count(?jamsFile) = 1)
LIMIT 200


    """
)

try:
    ret = sparql.queryAndConvert()

    for r in ret["results"]["bindings"]:
        print(r)
except Exception as e:
    print(e)

{'chocoId': {'type': 'literal', 'value': 'nottingham_141.jams'}, 'key_observation': {'type': 'literal', 'value': 'G:major'}}
{'chocoId': {'type': 'literal', 'value': 'nottingham_816.jams'}, 'key_observation': {'type': 'literal', 'value': 'D:major'}}
{'chocoId': {'type': 'literal', 'value': 'real-book_1625.jams'}, 'key_observation': {'type': 'literal', 'value': 'F:major'}}
{'chocoId': {'type': 'literal', 'value': 'real-book_589.jams'}, 'key_observation': {'type': 'literal', 'value': 'Eb:major'}}
{'chocoId': {'type': 'literal', 'value': 'real-book_2416.jams'}, 'key_observation': {'type': 'literal', 'value': 'G:major'}}
{'chocoId': {'type': 'literal', 'value': 'when-in-rome_343.jams'}, 'key_observation': {'type': 'literal', 'value': 'Eb:major'}}
{'chocoId': {'type': 'literal', 'value': 'when-in-rome_343.jams'}, 'key_observation': {'type': 'literal', 'value': 'C:minor'}}
{'chocoId': {'type': 'literal', 'value': 'when-in-rome_343.jams'}, 'key_observation': {'type': 'literal', 'value': 'Db:m

In [6]:
print(len(ret["results"]["bindings"]))

200


In [7]:
song_ids = [r['chocoId']['value'] for r in ret["results"]["bindings"]]
song_keys = [r['key_observation']['value'] for r in ret["results"]["bindings"]]

song_key_dict = {id: key for id, key in zip(song_ids, song_keys)}
song_key_dict

{'nottingham_141.jams': 'G:major',
 'nottingham_816.jams': 'D:major',
 'real-book_1625.jams': 'F:major',
 'real-book_589.jams': 'Eb:major',
 'real-book_2416.jams': 'G:major',
 'when-in-rome_343.jams': 'Bb:major',
 'when-in-rome_342.jams': 'Eb:major',
 'when-in-rome_344.jams': 'G:minor',
 'when-in-rome_345.jams': 'Cb:major',
 'nottingham_468.jams': 'A:minor',
 'jazz-corpus_49.jams': 'F:majoror',
 'jazz-corpus_19.jams': 'C:majoror',
 'jazz-corpus_8.jams': 'Eb:majoror',
 'jazz-corpus_100.jams': 'C#:minoror',
 'jazz-corpus_31.jams': 'F:majoror',
 'jazz-corpus_103.jams': 'Bb:majoror',
 'jazz-corpus_92.jams': 'C:majoror',
 'jazz-corpus_43.jams': 'C:minoror',
 'jazz-corpus_51.jams': 'G:majoror',
 'jazz-corpus_70.jams': 'F:majoror',
 'jazz-corpus_12.jams': 'C:majoror',
 'jazz-corpus_35.jams': 'Eb:majoror',
 'jazz-corpus_93.jams': 'C:majoror',
 'jazz-corpus_48.jams': 'Bb:majoror',
 'jazz-corpus_16.jams': 'Ab:majoror',
 'jazz-corpus_79.jams': 'D:minoror',
 'jazz-corpus_42.jams': 'F:majoror',
 'j

In [23]:
import json

inserted_ids = {'billboard_785.jams':'C#:min','billboard_739.jams':'Eb:', 'uspop2002_128': 'D:maj', 'uspop2002_108': 'Bb:maj', 'billboard_512':'Eb:maj'}

song_key_dict = {**song_key_dict, **inserted_ids}

# Convert and write JSON object to file
with open("./data/key_modes.json", "w") as outfile: 
    json.dump(song_key_dict, outfile)

In [24]:

songs = dict()
for song_id in song_key_dict.keys():
  sparql = SPARQLWrapper(
      "https://polifonia.disi.unibo.it/choco/sparql"
  )
  sparql.setReturnFormat(JSON)
  sparql.setQuery( f"""
  PREFIX rdf: <http://www.w3.org/1999/02/22-rdf-syntax-ns#>
  PREFIX rdfs: <http://www.w3.org/2000/01/rdf-schema#>
  PREFIX jams: <http://w3id.org/polifonia/ontology/jams/>
  PREFIX core: <http://w3id.org/polifonia/ontology/core/>
  PREFIX prov: <http://www.w3.org/ns/prov#>

  SELECT DISTINCT ?observationsType ?observationValue ?startTime ?startTimeType ?duration ?durationType
  WHERE {{
    bind("{song_id}" as ?queryID)
    ?jamsFile a jams:JAMSFile ;
      rdfs:label ?queryID .
    ?annotation a jams:JAMSAnnotation ;
      prov:wasDerivedFrom ?jamsFile ;
      jams:includesObservation ?observation ;
      jams:hasAnnotationType ?annotationType .
    ?observation rdfs:label ?observationValue ;
      jams:hasMusicTimeInterval [jams:hasMusicTimeDuration [ jams:hasValue ?duration ; jams:hasValueType ?durationType ] ;
        jams:hasMusicTimeStartIndex [ jams:hasMusicTimeIndexComponent [ jams:hasValue ?startTime ; jams:hasValueType ?startTimeType  ]]] .
    FILTER ( ?annotationType IN("chord", "chord_harte") ). 
  }}
  ORDER BY (?startTime)
      """ )

  try:
      ret = sparql.queryAndConvert()

      for r in ret["results"]["bindings"]:
          print(r)
  except Exception as e:
      print(e)
  songs[song_id] = ret["results"]["bindings"]

{'observationValue': {'type': 'literal', 'value': 'G:maj'}, 'startTime': {'datatype': 'http://www.w3.org/2001/XMLSchema#int', 'type': 'literal', 'value': '1'}, 'startTimeType': {'type': 'uri', 'value': 'http://w3id.org/polifonia/resource/ValueType/Beat'}, 'duration': {'datatype': 'http://www.w3.org/2001/XMLSchema#float', 'type': 'literal', 'value': '4.0'}, 'durationType': {'type': 'uri', 'value': 'http://w3id.org/polifonia/resource/ValueType/Beat'}}
{'observationValue': {'type': 'literal', 'value': 'E:min'}, 'startTime': {'datatype': 'http://www.w3.org/2001/XMLSchema#int', 'type': 'literal', 'value': '1'}, 'startTimeType': {'type': 'uri', 'value': 'http://w3id.org/polifonia/resource/ValueType/Beat'}, 'duration': {'datatype': 'http://www.w3.org/2001/XMLSchema#float', 'type': 'literal', 'value': '4.0'}, 'durationType': {'type': 'uri', 'value': 'http://w3id.org/polifonia/resource/ValueType/Beat'}}
{'observationValue': {'type': 'literal', 'value': 'A:min'}, 'startTime': {'datatype': 'http:

In [25]:

keys = dict()
for song_id in song_key_dict.keys():
  sparql = SPARQLWrapper(
      "https://polifonia.disi.unibo.it/choco/sparql"
  )
  sparql.setReturnFormat(JSON)
  sparql.setQuery( f"""
  PREFIX rdf: <http://www.w3.org/1999/02/22-rdf-syntax-ns#>
  PREFIX rdfs: <http://www.w3.org/2000/01/rdf-schema#>
  PREFIX jams: <http://w3id.org/polifonia/ontology/jams/>
  PREFIX core: <http://w3id.org/polifonia/ontology/core/>
  PREFIX prov: <http://www.w3.org/ns/prov#>

  SELECT DISTINCT ?observationValue ?startTime ?startTimeType ?duration ?durationType
  WHERE {{
    bind("{song_id}" as ?queryID)
    ?jamsFile a jams:JAMSFile ;
      rdfs:label ?queryID .
    ?annotation a jams:JAMSAnnotation ;
      prov:wasDerivedFrom ?jamsFile ;
      jams:includesObservation ?observation ;
      jams:hasAnnotationType "key_mode" .
    ?observation rdfs:label ?observationValue ;
      jams:hasMusicTimeInterval [jams:hasMusicTimeDuration [ jams:hasValue ?duration ; jams:hasValueType ?durationType ] ;
        jams:hasMusicTimeStartIndex [ jams:hasMusicTimeIndexComponent [ jams:hasValue ?startTime ; jams:hasValueType ?startTimeType  ]]] .
  }}
  ORDER BY (?startTime)
      """ )

  try:
      ret = sparql.queryAndConvert()

      for r in ret["results"]["bindings"]:
          print(r)
  except Exception as e:
      print(e)
  keys[song_id] = ret["results"]["bindings"]

{'observationValue': {'type': 'literal', 'value': 'G:major'}, 'startTime': {'datatype': 'http://www.w3.org/2001/XMLSchema#int', 'type': 'literal', 'value': '3'}, 'startTimeType': {'type': 'uri', 'value': 'http://w3id.org/polifonia/resource/ValueType/Beat'}, 'duration': {'datatype': 'http://www.w3.org/2001/XMLSchema#float', 'type': 'literal', 'value': '130.0'}, 'durationType': {'type': 'uri', 'value': 'http://w3id.org/polifonia/resource/ValueType/Beat'}}
{'observationValue': {'type': 'literal', 'value': 'G:major'}, 'startTime': {'datatype': 'http://www.w3.org/2001/XMLSchema#int', 'type': 'literal', 'value': '3'}, 'startTimeType': {'type': 'uri', 'value': 'http://w3id.org/polifonia/resource/choco/ValueType/Beat'}, 'duration': {'datatype': 'http://www.w3.org/2001/XMLSchema#float', 'type': 'literal', 'value': '130.0'}, 'durationType': {'type': 'uri', 'value': 'http://w3id.org/polifonia/resource/choco/ValueType/Beat'}}
{'observationValue': {'type': 'literal', 'value': 'D:major'}, 'startTime

In [26]:
def clean_function(s):
    s = s.replace('major', 'maj')
    s = s.replace('major', 'maj')
    s = s.replace('minor', 'min')
    s = s.replace('minor', 'min')
    s = s.replace('hdim77', 'hdim7')
    return s

for songId, song in songs.items():
    chord_sequence = [o['observationValue']['value'] for o in song]
    chord_duration= [o['duration']['value'] for o in song]
    with open(f'./data/chord_sequences/{songId}', "w") as chord_file:
        with open(f'./data/chord_durations/{songId}', "w") as duration_file:
            chord_file.write(clean_function(song_key_dict[songId])+'\n')
            for c, d  in zip(chord_sequence, chord_duration):
                if c != 'N':
                    chord_file.write(clean_function(c)+'\n')
                    duration_file.write(d+'\n')

In [12]:
pprint(chord_sequences)

Pretty printing has been turned OFF


In [16]:
# for songId, song in songs.items():
#     chord_duration= [o['duration']['value'] for o in song]
#     with open(f'./data/chord_durations/{songId}', "w") as file:
#         for c in chord_duration:
#             file.write(c+'\n')

In [27]:
from tpsd.tps_comparison import TpsComparison
from tpsd.tpsd_core import Tpsd
from tpsd.tpsd_comparison import TpsdComparison
from tpsd.util import open_harte, parse_mgu, get_corresponding_biab


with open('data/key_modes.json') as json_file:
    songs_key_dict = json.load(json_file)

tpsd_seq_dict = {}

for song, key in songs_key_dict.items():

    print(f'currently analyzing song {song}')

    chord_sequence_file = './data/chord_sequences/'+song

    chord_sequence, key = open_harte(chord_sequence_file)

    chord_sequence_filtered = [clean_function(chord) for chord in chord_sequence]


    def parse_txt_file_to_list(file_path):
        """
        Reads a .txt file and parses it into a list where each row is an element in the list.

        :param file_path: Path to the .txt file to be read
        :return: List containing each row of the file as an element
        """
        with open(file_path, 'r') as file:
            lines = file.readlines()
        # Remove any trailing newline characters
        lines = [int(float(line.strip())) for line in lines]
        return lines

    chord_duration_file = './data/chord_durations/'+ song
    chord_duration = parse_txt_file_to_list(chord_duration_file)



    print(f'sequence {chord_sequence_filtered} with duration {chord_duration}')
    tpsd = Tpsd(chord_sequence_filtered, key, chord_duration)

    tpsd_sequence = tpsd.sequence_area()
    tpsd_seq_dict[song] = tpsd_sequence


with open("./data/tpsd_seq_dict.json", "w") as outfile: 
    json.dump(tpsd_seq_dict, outfile)

currently analyzing song nottingham_141.jams
sequence ['G:maj', 'E:min', 'A:min', 'G:maj', 'D:maj', 'C:maj', 'C:maj', 'C:maj', 'G:maj', 'G:maj', 'A:min', 'E:min', 'C:maj', 'D:maj'] with duration [4, 4, 4, 8, 8, 4, 8, 4, 4, 8, 4, 4, 8, 8]
currently analyzing song nottingham_816.jams
sequence ['A:7', 'D:maj', 'D:maj', 'E:min', 'D:maj', 'E:min', 'G:maj', 'D:maj', 'G:maj', 'E:min', 'E:min', 'D:maj', 'A:7', 'D:maj', 'A:7', 'A:7', 'G:maj', 'G:maj'] with duration [4, 4, 2, 2, 8, 4, 4, 4, 4, 2, 4, 8, 4, 2, 2, 2, 1, 1]
currently analyzing song real-book_1625.jams
sequence ['G:min7', 'C:min7', 'Bb:7', 'A:hdim7', 'G:min7', 'G:min7/5', 'Ab:7', 'D:aug(b7)', 'A:aug(b7)', 'G:min7', 'D:7', 'G:min7', 'C:min7', 'Bb:7', 'A:hdim7', 'G:min7', 'G:min7/5', 'Ab:7', 'D:aug(b7)', 'A:aug(b7)', 'G:min7', 'D:7', 'Eb:7', 'F:7', 'D:7(#9)', 'C:7', 'G:min7', 'A:hdim7', 'G:7', 'D:aug(b7)', 'Eb:7', 'F:7', 'D:7(#9)', 'C:7', 'G:min7', 'A:hdim7', 'G:7', 'D:aug(b7)'] with duration [2, 2, 2, 2, 4, 12, 2, 2, 2, 12, 2, 2, 2, 2

UnexpectedCharacters: No terminal matches 'M' in the current parser context, at line 1 col 4

C#:Min
   ^
Expected one of: 
	* SHORTHAND
	* LPAR

Previous tokens: Token('COLON', ':')


In [20]:
from tslearn.metrics import dtw
# from itertools import product

with open('data/tpsd_seq_dict.json') as json_file:
    tpsd_seqs = json.load(json_file)

# combs = product(list(tpsd_seqs.keys())[:50], list(tpsd_seqs.keys())[:50])

# print(len(list(combs)))
min_dissmilarity = 99999999
s_1 = best_match = list(tpsd_seqs.keys())[1]
for s_2 in list(tpsd_seqs.keys())[2:]:
    sim_score = dtw(tpsd_seqs[s_1], tpsd_seqs[s_2])
    if sim_score < min_dissmilarity:
        best_match = s_2

/home/ritten/.pyenv/versions/3.11.7/envs/LaTeX-3.11.7/lib/python3.11/site-packages/tslearn/bases/bases.py:15: UserWarning: h5py not installed, hdf5 features will not be supported.
Install h5py to use hdf5 features: http://docs.h5py.org/
  warn(h5py_msg)


In [21]:
print(s_1)

print(s_2)

print(sim_score)

nottingham_816.jams
nottingham_584.jams
23.103030104295843
